In [23]:
import sys
import os
import logging
import logging.config
import json
import shutil
import matplotlib as mpl
import matplotlib.pyplot as plt
import pickle as pkl

# mpl.use('Agg')

import numpy as np

import copy
import sqlite3
import git
import torch
import torchvision
import torch.autograd as autograd
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

from misc.database import Database

from prediction_model import utils
from prediction_model.models.lstm_l0 import L0SeqLSTM
from prediction_model.models.fully_connected_l0 import L0FCN
from prediction_model.models.ntm_aio_l0 import EncapsulatedNTML0
from prediction_model.models.ntm_aio import EncapsulatedNTM
from prediction_model.objectives.sse import SSE
from prediction_model.objectives.logistic_loss import LogisticLoss

# plotting tools
from bokeh.io import output_notebook, show
from bokeh.layouts import gridplot
from bokeh.plotting import figure
from bokeh.models import CustomJS, Slider, ColumnDataSource, Whisker, Range1d

from datetime import datetime
from types import SimpleNamespace

output_notebook()

Loading BokehJS ...

In [6]:
def model_forward_fcn(X_train, y_train, model_p, objective_p, optimizer_p, l0_reg, backward=True, enable_gpu=False):
    model_out = []
    total_log_loss = None
    total_penalty = None
    
    X_train = torch.FloatTensor(X_train)
    y_train = torch.FloatTensor(y_train)
    if enable_gpu:
        X_train = X_train.cuda()
        y_train = y_train.cuda()

    out, (hidden, penalty) = model_p.forward(X_train)
#         ht, ct = hidden
    # print(x_t1, out)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    # print(out)

#     print(out.shape)
#     print(y_train.shape)
    log_loss = objective_p(out, y_train)

    if total_log_loss is None:
        total_log_loss = log_loss
        total_penalty = penalty
    else:
        total_log_loss += log_loss
        total_penalty += penalty

    model_out.append(out.cpu().data.numpy())

    total_loss = total_log_loss + l0_reg * total_penalty

    if backward:
        model.zero_grad()
        total_loss.backward()
        optimizer_p.step()

    if backward:
        total_penalty = np.sum(total_penalty.cpu().data.numpy())

    return model, \
           (np.sum(total_log_loss.cpu().data.numpy()), total_penalty), \
           model_out

In [7]:
def logistic_map(x, alpha):
    return alpha*x*(1-x)

def linear_map(x, alpha):
    return alpha*x

In [ ]:
seed = 0
alpha = 2
enable_gpu = True
l0_reg = 0.001

# for seed in range(args.n_seeds):
utils.common.set_global_seeds(seed)

model = L0FCN(input_bins=1,
              output_bins=1,
              fc_config=[20]*2,
              enable_gpu=True,
              test_mode=False)

if enable_gpu:
    model = model.cuda()

optimizer = optim.Adam(model.parameters(),
                       lr=1e-4,
                       weight_decay=0)

objective = SSE()

prev_loss = 0
epoch = 0
best_model = None
best_acc = 100
best_nparams = 0

while True:
    X_train = np.random.rand(50)
    y_train = np.array(list(map(lambda x: logistic_map(x, alpha), X_train)))

    X_train = X_train.reshape((-1, 1))
    y_train = y_train.reshape((-1, 1))

    model.train()
    model, (log_loss, penalty), model_out = model_forward_fcn(X_train,
                                                              y_train,
                                                              model,
                                                              objective,
                                                              optimizer,
                                                              l0_reg,
                                                              enable_gpu=enable_gpu)
    total_loss = (log_loss + l0_reg * penalty)

    # Validation
    model.eval()

    _, _, model_out = model_forward_fcn(X_train,
                                        y_train,
                                        model,
                                        objective,
                                        optimizer,
                                        l0_reg,
                                        enable_gpu=enable_gpu,
                                        backward=False)
#     predictions = (np.array(model_out) > 0.5).astype(int)
    predictions = np.array(model_out).flatten()
    actual = y_train.flatten()
    # print(actual == predictions)
    accuracy = np.sum(actual == predictions) / len(actual)
    model_nparams = model.get_l0_norm()

    # if accuracy > best_acc or (accuracy == best_acc and best_nparams > model_nparams):
    if log_loss <= best_acc and not (np.isnan(log_loss) or np.isnan(penalty)):
        best_model = copy.deepcopy(model.state_dict())
        best_acc = log_loss
        best_nparams = model_nparams
    div = X_train.shape[0]
    # print diagnostics
    if epoch % 100 == 0:
        model_out = np.array(model_out).flatten()
        print("")
        print("epoch: {} SSE loss: {}, l0 penalty: {} total loss: {}".format(epoch,
                                                                              log_loss / div,
                                                                              penalty / div,
                                                                              total_loss))
        print("accuracy: {}, actual: {}, predicted: {}, n_params: {} model_out: {}".format(accuracy,
                                                                                                 X_train.flatten(),
                                                                                                 predictions,
                                                                                                 model.get_l0_norm(),
                                                                                                 model_out))

    if np.abs(total_loss - prev_loss) <= 1e-9:
        print("Training converged: {}".format(np.abs(total_loss - prev_loss)))
        break

    prev_loss = total_loss
    epoch += 1

    if np.isnan(log_loss) or np.isnan(penalty):
        print("NaN detected")
        break
#     break

fc0
Gate mode: unique
fc1
Gate mode: unique
Gate mode: unique

epoch: 0 SSE loss: 0.04344484329223633, l0 penalty: 8.002297973632812 total loss: 2.572357063293457
accuracy: 0.0, actual: [0.5488135  0.71518937 0.60276338 0.54488318 0.4236548  0.64589411
 0.43758721 0.891773   0.96366276 0.38344152 0.79172504 0.52889492
 0.56804456 0.92559664 0.07103606 0.0871293  0.0202184  0.83261985
 0.77815675 0.87001215 0.97861834 0.79915856 0.46147936 0.78052918
 0.11827443 0.63992102 0.14335329 0.94466892 0.52184832 0.41466194
 0.26455561 0.77423369 0.45615033 0.56843395 0.0187898  0.6176355
 0.61209572 0.616934   0.94374808 0.6818203  0.3595079  0.43703195
 0.6976312  0.06022547 0.66676672 0.67063787 0.21038256 0.1289263
 0.31542835 0.36371077], predicted: [0.4910428  0.49057236 0.4908599  0.49105614 0.49139714 0.49071363
 0.4913607  0.49023575 0.49009866 0.49150643 0.49042645 0.4911103
 0.49097762 0.49017122 0.49235564 0.49231192 0.49249384 0.49034846
 0.49045232 0.49027723 0.49007136 0.4904123 


epoch: 500 SSE loss: 0.03274826765060425, l0 penalty: 7.96624755859375 total loss: 2.0357257604598997
accuracy: 0.0, actual: [0.8812033  0.53122103 0.8680575  0.77755907 0.96932112 0.92571412
 0.16927561 0.57996402 0.02856338 0.68828411 0.54150551 0.14278145
 0.66640611 0.36708941 0.09459162 0.00299151 0.60631975 0.79011012
 0.47399445 0.36391856 0.75603037 0.0063267  0.80624946 0.14631303
 0.2934198  0.61383733 0.8059898  0.14708033 0.66029159 0.40847581
 0.25638414 0.39374154 0.38463804 0.83570583 0.53699062 0.84165466
 0.16601442 0.83759583 0.3109018  0.71662891 0.49894272 0.59874476
 0.64255778 0.64013713 0.93336891 0.68057536 0.57611589 0.27045168
 0.83392349 0.2913378 ], predicted: [0.47308603 0.47369355 0.4731021  0.4732247  0.47297806 0.4730315
 0.4750256  0.47354308 0.47546566 0.47334763 0.47366178 0.47512782
 0.4733777  0.47427377 0.47528982 0.47553366 0.47346175 0.4732075
 0.47387195 0.47428566 0.47325438 0.47552484 0.47318524 0.47511426
 0.4745507  0.47345012 0.4731856  0.


epoch: 1000 SSE loss: 0.04090078353881836, l0 penalty: 7.931680297851562 total loss: 2.441623191833496
accuracy: 0.0, actual: [0.30764535 0.06200521 0.98878508 0.7190903  0.75756964 0.26375811
 0.81423212 0.56902059 0.45944772 0.13070624 0.31822656 0.3471398
 0.04941394 0.96384525 0.96475062 0.1106671  0.33928814 0.56340746
 0.48681865 0.56492329 0.86105383 0.81537125 0.41010138 0.52310581
 0.18856046 0.45604781 0.76245352 0.25340822 0.24580262 0.99679214
 0.22599421 0.962532   0.24860247 0.71298981 0.04488238 0.67372927
 0.41643382 0.51367789 0.51061752 0.37990148 0.01794764 0.80771941
 0.41246825 0.28481926 0.89542746 0.51598704 0.98335094 0.4560161
 0.71131126 0.09003222], predicted: [0.45191428 0.45253208 0.4505765  0.45102128 0.45095795 0.45202497
 0.45086467 0.4512683  0.45153114 0.45236012 0.4518875  0.45181456
 0.4525636  0.45061842 0.45061696 0.4524103  0.45183438 0.4512775
 0.4514621  0.45127502 0.45078763 0.4508628  0.45165566 0.45137057
 0.4522148  0.45153975 0.4509499  0.


epoch: 1500 SSE loss: 0.032360093593597414, l0 penalty: 7.897789306640625 total loss: 2.012894145011902
accuracy: 0.0, actual: [0.24392333 0.65495435 0.35150695 0.62498055 0.03401694 0.24540688
 0.22322093 0.0760436  0.83643934 0.88957214 0.18126889 0.78185092
 0.59343407 0.1847256  0.37908656 0.9475536  0.01381148 0.47050336
 0.78318807 0.62917569 0.36378382 0.02195515 0.8975815  0.50285664
 0.29962934 0.04863477 0.9932151  0.81687624 0.16885527 0.88573366
 0.06075629 0.8205812  0.25389633 0.99687541 0.04379909 0.15060614
 0.78009182 0.02238677 0.13359511 0.23338146 0.22705116 0.39122358
 0.77979902 0.18917251 0.32549157 0.44852835 0.3491879  0.64779936
 0.98710881 0.02330982], predicted: [0.4208361  0.4188671  0.42032686 0.41901138 0.42183006 0.42082903
 0.42093405 0.421631   0.41799384 0.41773823 0.4211327  0.41825643
 0.41916326 0.42111635 0.42019632 0.41707575 0.42192578 0.41976118
 0.41825002 0.4189912  0.42026874 0.42188722 0.4176997  0.419602
 0.42057237 0.4217609  0.41648993 


epoch: 2000 SSE loss: 0.02678309440612793, l0 penalty: 7.863179931640625 total loss: 1.7323137168884277
accuracy: 0.0, actual: [0.53525707 0.90404425 0.50239657 0.10087001 0.52758198 0.71122893
 0.31295428 0.05032535 0.12328206 0.77969075 0.94802187 0.71818603
 0.75389358 0.10964897 0.63814993 0.28945067 0.361702   0.00315978
 0.04352426 0.79419409 0.77746827 0.56411938 0.38736774 0.34514564
 0.41004102 0.06705749 0.97356847 0.06405922 0.10844153 0.47859636
 0.87148378 0.98030973 0.67780738 0.87716066 0.26757641 0.61586974
 0.44980164 0.61761576 0.80281463 0.03813337 0.29641567 0.33406014
 0.50907489 0.74504766 0.59307464 0.34360118 0.30266013 0.27967976
 0.92107048 0.87532113], predicted: [0.38442203 0.38015762 0.38469222 0.38799986 0.38448516 0.38280198
 0.38625148 0.38841695 0.38781494 0.38217017 0.37926894 0.38273776
 0.3824082  0.38792744 0.38347685 0.3864451  0.38585    0.3888063
 0.3884731  0.3820364  0.38219064 0.38416097 0.38563874 0.3859864
 0.3854521  0.38827887 0.37875307 

...


epoch: 224400 SSE loss: 0.008944047689437866, l0 penalty: 1.9126371765136718 total loss: 0.5428342432975769
accuracy: 0.0, actual: [0.7436305  0.04889006 0.02997181 0.76556207 0.18434257 0.3217514
 0.56827886 0.99059576 0.39674774 0.41556096 0.39463315 0.43952758
 0.99679314 0.90067019 0.53730489 0.97085977 0.93503992 0.72500437
 0.48866075 0.4576629  0.81225691 0.92716448 0.84744166 0.11967889
 0.19548896 0.04866028 0.63866199 0.31026512 0.55741023 0.30082514
 0.14452737 0.47895992 0.64412773 0.13744953 0.26415042 0.11767512
 0.71566267 0.31541965 0.12386565 0.15496043 0.82382069 0.91415886
 0.62407507 0.14271644 0.30385147 0.81688454 0.21921657 0.3455895
 0.65707689 0.93201644], predicted: [0.34054664 0.07436366 0.06058462 0.3069239  0.2791927  0.45215806
 0.48492348 0.08382983 0.48378432 0.48573813 0.4831498  0.48561025
 0.08055428 0.14663012 0.4850887  0.09508089 0.11898074 0.37043732
 0.48534817 0.48551354 0.24200031 0.12488822 0.1996804  0.1545403
 0.30296102 0.07418017 0.480901


epoch: 224900 SSE loss: 0.0011489864438772202, l0 penalty: 1.9101806640625 total loss: 0.152958355396986
accuracy: 0.0, actual: [0.3506782  0.50960308 0.3371935  0.39355051 0.00657772 0.78120044
 0.04140165 0.91441364 0.7534007  0.77256024 0.02407404 0.19054619
 0.91256127 0.76500246 0.77003685 0.49564883 0.53726975 0.91755162
 0.13232735 0.86309329 0.93930522 0.50567583 0.77526178 0.37586597
 0.76982231 0.42047883 0.03262853 0.4049048  0.85059384 0.31206531
 0.03589349 0.07778426 0.62705143 0.66710785 0.09363097 0.83406544
 0.70192236 0.42947262 0.28165317 0.89122239 0.80967451 0.37341741
 0.71573398 0.71796941 0.68518219 0.01849087 0.40466466 0.73829956
 0.57319513 0.53818161], predicted: [0.4694453  0.48491362 0.4649592  0.48287207 0.04675493 0.28215224
 0.06854913 0.13314505 0.3235019  0.29465812 0.05672785 0.2941259
 0.13466029 0.3058576  0.29837075 0.48498943 0.4847634  0.13061109
 0.17512257 0.18072495 0.11415289 0.484935   0.29071334 0.47755948
 0.2986877  0.48539782 0.0623031


epoch: 225400 SSE loss: 0.0029647189378738405, l0 penalty: 1.9074299621582032 total loss: 0.24360744500160217
accuracy: 0.0, actual: [0.4308698  0.0966278  0.71215227 0.16543004 0.72065723 0.22621747
 0.65136915 0.21970632 0.9025774  0.85766007 0.37917801 0.68767178
 0.90967922 0.09328355 0.73245827 0.97563582 0.54293611 0.2386982
 0.04430436 0.00437975 0.48615623 0.59824007 0.95288025 0.58136918
 0.19248392 0.84534266 0.78108066 0.74061073 0.67355916 0.55663795
 0.94651042 0.95674831 0.1489402  0.6253594  0.48131412 0.20200329
 0.64522538 0.38946453 0.69857312 0.46638566 0.59814014 0.36952672
 0.63570387 0.20603583 0.14921533 0.42324847 0.26830894 0.42639012
 0.41579664 0.86092325], predicted: [0.48587543 0.12267361 0.39525703 0.23827676 0.38103905 0.3434529
 0.47861856 0.33612362 0.14606306 0.19006151 0.4795085  0.43710247
 0.13993688 0.11852318 0.3616483  0.09278163 0.48528734 0.35771018
 0.07045639 0.04534966 0.48558527 0.48499715 0.10717378 0.48508567
 0.29840654 0.20376962 0.286


epoch: 225900 SSE loss: 0.0011877818405628205, l0 penalty: 1.904945068359375 total loss: 0.15463634544610977
accuracy: 0.0, actual: [0.44942839 0.28045371 0.64824285 0.35289896 0.43013796 0.85097094
 0.01151022 0.85031308 0.98755351 0.8034555  0.93889346 0.65526797
 0.16974639 0.3857316  0.19281505 0.81667903 0.58298655 0.38151152
 0.97198954 0.73464171 0.59933715 0.9007652  0.23578967 0.44582262
 0.41093265 0.69827471 0.14846388 0.03848407 0.44703318 0.49859197
 0.87002764 0.71025578 0.26291315 0.90794332 0.65614575 0.40249659
 0.13684154 0.5292797  0.56805424 0.26068079 0.69674355 0.63191757
 0.43672783 0.13557628 0.95526148 0.86352048 0.46270481 0.05338659
 0.45754576 0.79097571], predicted: [0.4858403  0.40557703 0.47950926 0.47080562 0.48594296 0.19562592
 0.04893633 0.19635852 0.08477622 0.2538758  0.11555129 0.47716904
 0.24781743 0.4812802  0.29918012 0.23658335 0.48513    0.48001677
 0.09370993 0.35624313 0.48504305 0.14606796 0.3538591  0.48585954
 0.48604512 0.41710106 0.20


epoch: 226400 SSE loss: 0.010862784385681152, l0 penalty: 1.9025057983398437 total loss: 0.6382645092010498
accuracy: 0.0, actual: [1.28776616e-01 3.11336303e-01 2.63418237e-01 6.67438868e-01
 9.81746947e-01 5.42462363e-01 2.49115161e-01 2.17293896e-01
 3.12144287e-01 7.48894993e-01 7.86184617e-01 5.76255019e-01
 6.35706666e-01 8.25265922e-01 5.57216000e-01 2.59991235e-01
 7.75958192e-01 4.38533981e-01 2.12409699e-02 3.70849557e-01
 6.78342622e-01 2.79971337e-01 4.37332399e-01 2.90225748e-01
 2.64273377e-04 1.20756716e-01 6.55691055e-01 8.77121579e-01
 7.57381347e-01 5.40824070e-01 8.98469422e-01 9.78365018e-01
 7.91091102e-01 2.54098351e-01 5.76591388e-01 6.98572399e-03
 4.27631242e-01 1.49874981e-02 6.10258036e-01 3.84023638e-01
 9.26393264e-01 9.94288258e-01 4.02610226e-01 6.90702392e-01
 8.98529718e-01 8.72693422e-01 3.31645952e-01 3.42228597e-01
 2.25652508e-01 2.77096561e-01], predicted: [0.16739613 0.43931872 0.38501343 0.46866906 0.08736084 0.48482618
 0.36809283 0.3316391  0.

In [15]:
model_test = L0FCN(input_bins=1,
                  output_bins=1,
                  fc_config=[20]*2,
                  enable_gpu=True,
                  test_mode=False)
model_test.load_state_dict(best_model)

fc0
Gate mode: unique
fc1
Gate mode: unique
Gate mode: unique


<All keys matched successfully>

In [16]:
model_test.get_l0_norm()

tensor(65)

In [29]:
model_test = model_test.cuda()

model_test.eval()

x = np.arange(0, 1, 0.01)
y = list(map(lambda val: logistic_map(val, alpha), x))
y_pred = None
k = 1
for i in range(k):
    y_pred_k = []
    for x_val in x:
        x_val = torch.FloatTensor([x_val]).cuda()
        out, _ = model_test.forward(x_val)
        out = torch.clamp(out, -8, 8)
        out = F.sigmoid(out)
        y_pred_k.append(out.data.cpu().numpy()[0])
    
    if y_pred is None:
        y_pred = np.array(y_pred_k)
    else:
        y_pred += np.array(y_pred_k)

y_pred = y_pred/k
plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,wheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(x,
          y)
plot.line(x,
          y_pred,
         line_color="orange")
plot.x(X_train.flatten(),
       y_train.flatten())

plot.xaxis.axis_label = 'x'
plot.yaxis.axis_label = 'f(x)'

show(plot)

In [30]:
series_pred = []
series_pred_in = []
series_actual = []
lambda_series_pred = []
lambda_series_actual = []
x_t_m = 0.7
x_t_a = x_t_m
x_t_i = x_t_m
n_points = 500

step = 0
tot_steps = 5

for i in range(n_points):
    x_val = torch.FloatTensor([x_t_m]).cuda()
    out, _ = model_test.forward(x_val)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    lambda_series_pred.append(out.data.cpu().numpy()[0]/(x_t_m*(1-x_t_m)))
    x_t_m = out.data.cpu().numpy()[0]
    series_pred.append(x_t_m)
    
    if step >= tot_steps:
        x_t_i = x_t_a
        step = 0
    
    x_val = torch.FloatTensor([x_t_i]).cuda()
    out, _ = model_test.forward(x_val)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    x_t_i = out.data.cpu().numpy()[0]
    series_pred_in.append(x_t_i)
    step += 1
    
    lambda_series_actual.append(logistic_map(x_t_a, alpha=alpha)/(x_t_a*(1-x_t_a)))
    x_t_a = logistic_map(x_t_a, alpha=alpha)
    series_actual.append(x_t_a)

plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,xwheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(range(n_points),
          series_actual)
plot.line(range(n_points),
          series_pred,
          line_color="orange")
plot.line(range(n_points),
          series_pred_in,
          line_color="red")

plot.xaxis.axis_label = 'step'
plot.yaxis.axis_label = 'f(x)'

plot.y_range = Range1d(0, 1)

show(plot)

mean_lambda_pred = [ np.mean(lambda_series_pred[:i]) 
                    for i in range(1, len(lambda_series_pred)) ]

plot = figure(**plot_options)
plot.line(range(n_points),
          lambda_series_actual)
plot.line(range(n_points),
          lambda_series_pred,
          line_color="orange")
plot.line(range(n_points),
          mean_lambda_pred,
          line_color="red")

plot.xaxis.axis_label = 'step'
plot.yaxis.axis_label = 'lambda'

show(plot)

In [32]:
n_points = 500

step = 0
tot_steps = 10
step_stderr = []

for step in range(1, tot_steps):
    print(step)
    step_err = []
    for i in range(n_points):  
        x_t_m = series_actual[i]
        err = []
        for pred_step in range(step):
            x_val = torch.FloatTensor([x_t_m]).cuda()
            out, _ = model_test.forward(x_val)
            out = torch.clamp(out, -8, 8)
            out = F.sigmoid(out)
            lambda_series_pred.append(out.data.cpu().numpy()[0]/(x_t_m*(1-x_t_m)))
            x_t_m = out.data.cpu().numpy()[0]
            
            try:
                err.append(np.abs(series_actual[i+pred_step+1] - x_t_m))
            except IndexError:
                break
        step_err.append(np.mean(err))
    step_err = np.array(step_err)
    step_err = step_err[~np.isnan(step_err)]
    step_stderr.append(np.mean(np.array(step_err)))
#     print(step_err)
#     print(step_stderr)
            
plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,xwheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(range(tot_steps),
          step_stderr,
         line_width=2)

plot.xaxis.axis_label = 'prediction steps'
plot.yaxis.axis_label = 'standard_error'

show(plot)

1
2
3
4
5
6
7
8
9


In [ ]:
step_stderr